In [1]:
#Librerias necesarias para implementacion de algoritmo genetico
from __future__ import print_function

from evolver import Evolver

from tqdm import tqdm

import logging

import sys


# Aplicacion del Modelo
Aqui se aplica directamente el modelo descrito implementando el algoritmo genetico

In [2]:
#Librerias necesarias para trabajar con datasets
import pandas as pd
import numpy as np
from sklearn import linear_model, model_selection

#Librerias necesarias para aplicar redes neuronales
import tensorflow as tf
pd.set_option('display.max_columns', None)
df= pd.read_csv("Historial_Alumnos.csv", sep=",",index_col=False)
df.head()

id_anony Cod.Car.Sec  Cod.Car.Sec Codificado  Materia_1  \
0      2838  MCT-PLS13                     28.0  CALCULO 1   
1      4037  MCT-PLS13                     28.0  CALCULO 1   
2      4061  MCT-PLS13                     28.0  CALCULO 1   
3      4062  MCT-PLS13                     28.0  CALCULO 1   
4      4065  MCT-PLS13                     28.0  CALCULO 1   

   Materia_1 codificada  Anho_F_1  ciclo_F_1  Recursante_1  P1_F_1  P2_F_1  \
0                  33.0    2013.0        2.0           1.0     0.0    17.0   
1                  33.0    2015.0        2.0           1.0    16.0    19.0   
2                  33.0    2015.0        2.0           1.0    14.0    27.0   
3                  33.0    2015.0        2.0           1.0     5.0    24.0   
4                  33.0    2015.0        2.0           1.0    19.0    30.0   

   T_F_1  NotaFinal_1  Materia_1 Nota=1  Materia_1 Nota=2  Materia_1 Nota=3  \
0    8.0          2.0               0.0               1.0               0.0   
1    8.0          5.0               0.0               0.0               0.0   
2    8.0          3.0               0.0               0.0               1.0   
3    6.0          2.0               0.0               1.0               0.0   
4    9.0          5.0               0.0               0.0               0.0   

   Materia_1 Nota=4  Materia_1 Nota=5  Abandono la Materia 1  Materia_2  \
0               0.0               0.0                    1.0  CALCULO 2   
1               0.0               1.0                    0.0  CALCULO 2   
2               0.0               0.0                    0.0  CALCULO 2   
3               0.0               0.0                    0.0  CALCULO 2   
4               0.0               1.0                    0.0  CALCULO 2   

   Materia_2 codificada  Anho_F_2  ciclo_F_2  Recursante_2  P1_F_2  P2_F_2  \
0                  34.0    2014.0        1.0           1.0    11.0    16.0   
1                  34.0    2016.0        1.0           1.0    22.0    31.0   
2                  34.0    2016.0        1.0           1.0    13.0    23.0   
3                  34.0    2016.0        1.0           1.0    21.0    19.0   
4                  34.0    2016.0        1.0           1.0    24.0    29.0   

   T_F_2  NotaFinal_2  Materia_2 Nota=1  Materia_2 Nota=2  Materia_2 Nota=3  \
0    8.0          2.0               0.0               1.0               0.0   
1    7.0          5.0               0.0               0.0               0.0   
2    5.0          2.0               0.0               1.0               0.0   
3    5.0          2.0               0.0               1.0               0.0   
4    9.0          5.0               0.0               0.0               0.0   

   Materia_2 Nota=4  Materia_2 Nota=5  Abandono la Materia 2  Materia_3  \
0               0.0               0.0                    0.0  CALCULO 3   
1               0.0               1.0                    0.0  CALCULO 3   
2               0.0               0.0                    0.0  CALCULO 3   
3               0.0               0.0                    0.0  CALCULO 3   
4               0.0               1.0                    0.0  CALCULO 3   

   Materia_3 codificada  Anho_F_3  ciclo_F_3  Recursante_3  P1_F_3  P2_F_3  \
0                  35.0    2016.0        2.0           1.0    10.0     7.0   
1                  35.0    2016.0        2.0           1.0     6.0     9.0   
2                  35.0    2016.0        2.0           1.0    17.0    10.0   
3                  35.0    2016.0        2.0           1.0     5.0    18.0   
4                  35.0    2016.0        2.0           1.0    22.0    20.0   

   T_F_3  NotaFinal_3  Materia_3 Nota=1  Materia_3 Nota=2  Materia_3 Nota=3  \
0    2.0          2.0               0.0               1.0               0.0   
1    8.0          4.0               0.0               0.0               0.0   
2    8.0          2.0               0.0               1.0               0.0   
3    6.0          2.0               0.0               1

Antes que nada, es necesario preparar los datos que la red neuronal solicita para poder procesar la opcion mas viable para nuestro analisis

In [3]:
data=df[['Materia_1 codificada','Anho_F_1','ciclo_F_1','Recursante_1','P1_F_1','P2_F_1','T_F_1','NotaFinal_1','Abandono la Materia 1','Materia_2 codificada','Anho_F_2','ciclo_F_2','Recursante_2','P1_F_2','P2_F_2','T_F_2','NotaFinal_2','Abandono la Materia 2']]

[filas,columnas]=data.shape
labels=df[['Materia_3 Nota=3']]

#Como labels figura como string, es necesario cambiarlos a valores enteros
data = np.array(data)
labels = np.array(labels)
labels=np.ravel(labels)

#Verificamos las dimensiones de data y labels
display(np.shape(labels))
display(np.shape(data))

(56,)

(56, 18)

Los datos que el algoritmo genetico solicita a lo largo de su procesamiento son data, labels y columnas. Para facilitar dichos datos del notebook al algoritmo genetico, se emplea la libreria pickle

In [4]:
from pickle import dump,load
dump(data, open('data.pkl', 'wb'))
dump(labels, open('labels.pkl', 'wb'))
dump(columnas, open('columnas.pkl', 'wb'))

Una vez definidos apropiadamente estos parametros, se procede a realizar el procesamiento con el algoritmo genetico

In [5]:
import main as ge
lista=ge.main()

07/07/2021 10:25:22 AM - INFO - ***generate(generations, population, all_possible_genes, dataset)***
07/07/2021 10:25:22 AM - INFO - ***Now in generation 1 of 50***
07/07/2021 10:25:22 AM - INFO - --------------------------------------------------------------------------------
07/07/2021 10:25:22 AM - INFO - {'nb_layers': 1, 'activation': 'relu', 'optimizer': 'adamax', 'nb_neurons': [32, 64, 128, 32, 64, 16]}
07/07/2021 10:25:22 AM - INFO - Acc: 0.00%
07/07/2021 10:25:22 AM - INFO - UniID: 1
07/07/2021 10:25:22 AM - INFO - Mom and Dad: 0 0
07/07/2021 10:25:22 AM - INFO - Gen: 1
07/07/2021 10:25:22 AM - INFO - Hash: 0c1c4658334acbb32d311589f65205b8
07/07/2021 10:25:22 AM - INFO - {'nb_layers': 3, 'activation': 'sigmoid', 'optimizer': 'adam', 'nb_neurons': [64, 128, 16, 64, 32, 16]}
07/07/2021 10:25:22 AM - INFO - Acc: 0.00%
07/07/2021 10:25:22 AM - INFO - UniID: 2
07/07/2021 10:25:22 AM - INFO - Mom and Dad: 0 0
07/07/2021 10:25:22 AM - INFO - Gen: 1
07/07/2021 10:25:22 AM - INFO - Hash

07/07/2021 10:25:22 AM - INFO - {'nb_layers': 4, 'activation': 'relu', 'optimizer': 'adamax', 'nb_neurons': [128, 128, 64, 32, 64, 64]}
07/07/2021 10:25:22 AM - INFO - Acc: 0.00%
07/07/2021 10:25:22 AM - INFO - UniID: 22
07/07/2021 10:25:22 AM - INFO - Mom and Dad: 0 0
07/07/2021 10:25:22 AM - INFO - Gen: 1
07/07/2021 10:25:22 AM - INFO - Hash: a9113bf140eebec8bed7e3a1cb319e1a
07/07/2021 10:25:22 AM - INFO - {'nb_layers': 4, 'activation': 'softmax', 'optimizer': 'adamax', 'nb_neurons': [32, 128, 16, 32, 32, 64]}
07/07/2021 10:25:22 AM - INFO - Acc: 0.00%
07/07/2021 10:25:22 AM - INFO - UniID: 23
07/07/2021 10:25:22 AM - INFO - Mom and Dad: 0 0
07/07/2021 10:25:22 AM - INFO - Gen: 1
07/07/2021 10:25:22 AM - INFO - Hash: 21581e6c2dbfc90ea14cf3809155dbb1
07/07/2021 10:25:22 AM - INFO - {'nb_layers': 3, 'activation': 'relu', 'optimizer': 'adamax', 'nb_neurons': [128, 16, 128, 64, 32, 16]}
07/07/2021 10:25:22 AM - INFO - Acc: 0.00%
07/07/2021 10:25:22 AM - INFO - UniID: 24
07/07/2021 10:25:

***Dataset: dataset
***Evolving for 50 generations with population size = 30***
(44,)
(44, 18)
(44, 2)
(44, 18)
(44, 18)
(44, 2)
Epoch 1/50
1/1 [==============================] - 0s 142ms/step - loss: 0.6899 - accuracy: 0.5000 - val_loss: 0.5936 - val_accuracy: 0.7500
Epoch 2/50
1/1 [==============================] - 0s 11ms/step - loss: 0.6741 - accuracy: 0.5909 - val_loss: 0.5802 - val_accuracy: 0.8333
Epoch 3/50
1/1 [==============================] - 0s 12ms/step - loss: 0.6889 - accuracy: 0.5455 - val_loss: 0.5680 - val_accuracy: 0.8333


  3%|▎         | 1/30 [00:00<00:28,  1.03it/s]07/07/2021 10:25:23 AM - INFO - Getting Keras datasets
07/07/2021 10:25:23 AM - INFO - Compling Keras model
07/07/2021 10:25:23 AM - INFO - Architecture:[64, 128, 16, 64, 32, 16],sigmoid,adam,3


Test loss: 0.5679516196250916
Test accuracy: 0.8333333134651184

 Modelo mas eficiente creado 

(44,)
(44, 18)
(44, 2)
(44, 18)
(44, 18)
(44, 2)
Epoch 1/50
1/1 [==============================] - 0s 142ms/step - loss: 0.8244 - accuracy: 0.4091 - val_loss: 0.8590 - val_accuracy: 0.0000e+00
Epoch 2/50
1/1 [==============================] - 0s 15ms/step - loss: 0.7886 - accuracy: 0.4773 - val_loss: 0.7853 - val_accuracy: 0.0000e+00
Epoch 3/50
1/1 [==============================] - 0s 14ms/step - loss: 0.7802 - accuracy: 0.4318 - val_loss: 0.7175 - val_accuracy: 0.0000e+00
Epoch 4/50
1/1 [==============================] - 0s 12ms/step - loss: 0.7464 - accuracy: 0.3864 - val_loss: 0.6559 - val_accuracy: 1.0000
Epoch 5/50
1/1 [==============================] - 0s 15ms/step - loss: 0.7049 - accuracy: 0.5227 - val_loss: 0.6001 - val_accuracy: 1.0000
Epoch 6/50
1/1 [==============================] - 0s 15ms/step - loss: 0.6306 - accuracy: 0.6136 - val_loss: 0.5500 - val_accuracy: 1.0000
Epoch 7/

...

Test loss: 0.19620990753173828
Test accuracy: 1.0
(44,)
(44, 18)
(44, 2)
(44, 18)
(44, 18)
(44, 2)
Epoch 1/50
1/1 [==============================] - 0s 95ms/step - loss: 1.0391 - accuracy: 0.2955 - val_loss: 1.1593 - val_accuracy: 0.0000e+00
Epoch 2/50
1/1 [==============================] - 0s 12ms/step - loss: 1.0069 - accuracy: 0.2955 - val_loss: 1.0471 - val_accuracy: 0.0000e+00
Epoch 3/50
1/1 [==============================] - 0s 10ms/step - loss: 0.9168 - accuracy: 0.2500 - val_loss: 0.9427 - val_accuracy: 0.0000e+00
Epoch 4/50
1/1 [==============================] - 0s 10ms/step - loss: 0.8491 - accuracy: 0.4318 - val_loss: 0.8452 - val_accuracy: 0.0000e+00
Epoch 5/50
1/1 [==============================] - 0s 10ms/step - loss: 0.8073 - accuracy: 0.3409 - val_loss: 0.7552 - val_accuracy: 0.0000e+00
Epoch 6/50
1/1 [==============================] - 0s 10ms/step - loss: 0.8098 - accuracy: 0.3636 - val_loss: 0.6727 - val_accuracy: 1.0000
Epoch 7/50
1/1 [==============================]

 98%|█████████▊| 50/51 [00:32<00:00,  1.44it/s]07/07/2021 10:52:41 AM - INFO - Getting Keras datasets
07/07/2021 10:52:41 AM - INFO - Compling Keras model
07/07/2021 10:52:41 AM - INFO - Architecture:[64, 128, 32, 32, 16, 128],sigmoid,adamax,3


Test loss: 0.3812286853790283
Test accuracy: 1.0
(44,)
(44, 18)
(44, 2)
(44, 18)
(44, 18)
(44, 2)
Epoch 1/50
1/1 [==============================] - 0s 269ms/step - loss: 0.5676 - accuracy: 0.7727 - val_loss: 0.2694 - val_accuracy: 1.0000
Epoch 2/50
1/1 [==============================] - 0s 10ms/step - loss: 0.6152 - accuracy: 0.7500 - val_loss: 0.2891 - val_accuracy: 1.0000
Epoch 3/50
1/1 [==============================] - 0s 10ms/step - loss: 0.6655 - accuracy: 0.7273 - val_loss: 0.2964 - val_accuracy: 1.0000


100%|██████████| 51/51 [00:32<00:00,  1.55it/s]
07/07/2021 10:52:42 AM - INFO - Generation average: 88.24%
07/07/2021 10:52:42 AM - INFO - --------------------------------------------------------------------------------
07/07/2021 10:52:42 AM - INFO - --------------------------------------------------------------------------------
07/07/2021 10:52:42 AM - INFO - {'nb_layers': 3, 'activation': 'sigmoid', 'optimizer': 'adam', 'nb_neurons': [64, 128, 16, 64, 32, 16]}
07/07/2021 10:52:42 AM - INFO - Acc: 100.00%
07/07/2021 10:52:42 AM - INFO - UniID: 2
07/07/2021 10:52:42 AM - INFO - Mom and Dad: 0 0
07/07/2021 10:52:42 AM - INFO - Gen: 1
07/07/2021 10:52:42 AM - INFO - Hash: 5a92b8f4f63af8902eef73049d513a21
07/07/2021 10:52:42 AM - INFO - {'nb_layers': 5, 'activation': 'softmax', 'optimizer': 'adam', 'nb_neurons': [32, 16, 16, 16, 64, 64]}
07/07/2021 10:52:42 AM - INFO - Acc: 100.00%
07/07/2021 10:52:42 AM - INFO - UniID: 3
07/07/2021 10:52:42 AM - INFO - Mom and Dad: 0 0
07/07/2021 10:52

Test loss: 0.2963784337043762
Test accuracy: 1.0
